In [1]:
pip install selenium

Note: you may need to restart the kernel to use updated packages.


In [2]:
from bs4 import BeautifulSoup
import requests
import time
import re
import json
from selenium import webdriver
from selenium.webdriver import Chrome
from selenium.webdriver.common.by import By
from tqdm import tqdm

In [15]:
def make_driver():
    options=webdriver.ChromeOptions()
    options.add_argument("--headless")
    return webdriver.Chrome(options=options)

driver=make_driver()
url="https://www.ycombinator.com/companies"

def get_url():
    driver.get(url)
    
def click_see_all_options():
    time.sleep(5)
    see_all_options= driver.find_element(By.CSS_SELECTOR, 'a._showMoreLess_99gj3_241')
    see_all_options.click()

def compile_batches():
    pattern=re.compile(r'^(|W|S|IK)[012]')
    filter_checkbox=driver.find_elements(By.XPATH,'//label')
    for checkbox in filter_checkbox:
        if pattern.match(checkbox.text):
            yield checkbox

def scroll_to_bottom(driver):
    last_height=driver.execute_script("return document.body.scrollHeight")
    while True:
        driver.execute_script("window.scrollTo(0,document.body.scrollHeight);")
        time.sleep(5)
        new_height=driver.execute_script("return document.body.scrollHeight")
        if new_height==last_height:
            break
        last_height=new_height
        
def fetch_url_paths():
    elements = driver.find_elements(
        By.XPATH, ('//a[contains(@href,"/companies/") and not(contains(@href,"founders"))]'))
    for url in elements:
        yield url.get_attribute('href')

def write_urls_to_file(url_list):
    with open('company_urls.txt', 'w') as f:
        for url in url_list:
            f.write(url + '\n')
def read_urls_from_file():
    url_list = [] 
    with open('company_urls.txt', 'r') as f:
        for line in f:
            url_list.append(line.strip())
    return url_list   

def yc_links_extractor():
    try:
        get_url()
        click_see_all_options()
        batches=compile_batches()
        all_company_urls=[]
    
        for b in tqdm(list(batches)):
            b.click()
            scroll_to_bottom(driver)
            urls = fetch_url_paths()
            all_company_urls.extend(urls)
            b.click()
        write_urls_to_file(all_company_urls)
        print(f"Total company URLs extracted: {len(all_company_urls)}")
    except Exception as e:
        print(f"An error occurred: {str(e)}")
    finally:
        driver.quit()


if __name__=='__main__':
    yc_links_extractor()

100%|██████████| 39/39 [22:59<00:00, 35.37s/it]


Total company URLs extracted: 4663


In [ ]:
def scrape_company_website(url):
    try:
        response=requests.get(url)
        response.raise_for_status()
    except requests.exceptions.RequestException as e:
        print(f"An error occurred while requesting {url}: {e}")
        return None
    
    if response.status_code==200:
        soup=BeautifulSoup(response.content,'html.parser')
        
        company_name=soup.find('h1',class_="font-extralight").text.strip()
        tagline=soup.find('h3',class_="sm:block md:hidden").text.strip()
        
        description=[]
        description_tags=soup.find('p',class_="whitespace-pre-line")
        if description_tags:
            descriptions=description_tags.get_text(separator="",strip=True)
            description=descriptions.split('\n')[0]
        else:
            print("description not found")
        batches= soup.find('a', href=lambda href: href and 'batch'in href)
        batch=batches.find('span').text.strip() if batches else None
        industry_tags = [a.text.strip() for a in soup.find_all('a', href=lambda href: href and 'industry' in href)]
        company_type = soup.find('div', class_='flex flex-row items-center justify-between').text.strip()
        
        location=soup.find('span',string="Location:")
        locations=location.find_next_sibling('span').text.strip()
        
        website_link=soup.find('div', class_='inline-block group-hover:underline')
        website=website_link.text.strip()

        founded=soup.find('span',string="Founded:")
        founded_year=founded.find_next_sibling('span').text.strip()
        
        team_size=soup.find('span',string="Team Size:")
        team_size_value=team_size.find_next_sibling('span').text.strip()
        
        social_media=soup.find('div',class_="space-x-2")
        social_media_url={}
        if social_media:
            links=social_media.find_all('a')
            for link in links:
                if 'linkedin' in link['href']:
                    social_media_url['linkedin']=link['href']
                elif 'twitter' in link['href']:
                    social_media_url['twitter']=link['href']
                elif 'facebook' in link['href']:
                    social_media_url['facebook']=link['href']
                elif 'crunchbase' in link['href']:
                    social_media_url['crunchbase']=link['href']
        
        founder_name=[]
        founder_tags=soup.find('h3',class_="text-lg font-bold")
        if founder_tags:
            tags=founder_tags.text.strip()
            name=tags.split(',',1)[0] if ',' in tags else tags.strip()
            founder_name.append(name)
        biography=[]
        biographies=soup.find('p',class_="prose max-w-full whitespace-pre-line")
        if biographies:
            biography=[bio.text.strip().split('\n')[:1] for bio in biographies]
        else:
            print("bio not found")
            
        social_media_profile=soup.find('div',class_="mt-1 space-x-2")
        social_media_profile_data={}
        if social_media_profile:
            links=social_media_profile.find_all('a')
            for link in links:
                if 'linkedin' in link['href']:
                    social_media_profile_data['linkedin']=link['href']
                elif 'twitter' in link['href']:
                    social_media_profile_data['twitter']=link['href']
        founders_info=[]
        founder_data = {
                    "Name":founder_name,
                    "Biography": biography,
                    "LinkedIn Profile": social_media_profile_data.get('linkedin'),
                    "Twitter Profile": social_media_profile_data.get('twitter')
                }
        founders_info.append(founder_data)
                    
        company_data={
           "company":{
              "Company Name": company_name,
              "Tagline": tagline,
              "Description":description,
              "batch":batch,
              "company type":company_type,
              "industry tags":industry_tags,
              "Location": locations,
              "website":website,
              "Founded": founded_year,
              "Team Size": team_size_value,
              "social media profiles":{
                    "LinkedIn": social_media_url.get('linkedin'),
                    "Twitter": social_media_url.get('twitter'),
                    "Facebook": social_media_url.get('facebook'),
                    "Crunchbase": social_media_url.get('crunchbase')
              }
           },
            "founders":founders_info
        
    }  
        print(json.dumps(company_data,indent=4))
        return company_data

if __name__ == '__main__':
    all_company_urls=read_urls_from_file()
    all_company_data=[]
    for url in all_company_urls:
        company_data=scrape_company_website(url)
        all_company_data.append(company_data)

{
    "company": {
        "Company Name": "Alacrity",
        "Tagline": "AI Based Account Takeover Prevention Platform",
        "Description": "We are building a safer internet. Account Takeovers remain a problem - despite 2FA and all the fraud prevention platforms out there today. We are building the next generation of fraud prevention and identity tools. Having fought fraud at the largest scale at some of the biggest companies in the world, we are now building what we wish we had and giving those tools to everyone.",
        "batch": "W24",
        "company type": "Active",
        "industry tags": [
            "identity",
            "fraud-prevention",
            "fraud-detection"
        ],
        "Location": "San Francisco",
        "website": "http://www.joinalacrity.com",
        "Founded": "2024",
        "Team Size": "2",
        "social media profiles": {
            "LinkedIn": "https://www.linkedin.com/company/100487698/admin",
            "Twitter": null,
          

{
    "company": {
        "Company Name": "RetailReady",
        "Tagline": "An AI-powered supply chain compliance engine",
        "Description": "Every time workers in a warehouse box an order, they reference a 100 page manual with instructions like where to put the shipping label. RetailReady replaces the instruction manual with a tablet application.",
        "batch": "W24",
        "company type": "Active",
        "industry tags": [
            "b2b",
            "compliance",
            "logistics",
            "supply-chain",
            "ai"
        ],
        "Location": "",
        "website": "https://www.retailreadyai.com/",
        "Founded": "2024",
        "Team Size": "3",
        "social media profiles": {
            "LinkedIn": "https://www.linkedin.com/company/retailreadyai/",
            "Twitter": null,
            "Facebook": null,
            "Crunchbase": null
        }
    },
    "founders": [
        {
            "Name": [
                "Elle Smyth"
    

{
    "company": {
        "Company Name": "Yarn",
        "Tagline": "Make sales and marketing videos with AI.",
        "Description": "Yarn uses AI to help founders, salespeople, and marketers make product and sales videos.\r",
        "batch": "W24",
        "company type": "Active",
        "industry tags": [
            "artificial-intelligence",
            "b2b",
            "sales",
            "video",
            "marketing"
        ],
        "Location": "San Francisco",
        "website": "https://www.yarn.so",
        "Founded": "2023",
        "Team Size": "2",
        "social media profiles": {
            "LinkedIn": "https://www.linkedin.com/company/yarn-so",
            "Twitter": "https://twitter.com/yarn_so",
            "Facebook": null,
            "Crunchbase": null
        }
    },
    "founders": [
        {
            "Name": [
                "Jasper Story"
            ],
            "Biography": [
                [
                    "Co-founder and CEO a

{
    "company": {
        "Company Name": "Dragoneye",
        "Tagline": "Helping devs build computer vision models automatically",
        "Description": "Dragoneye helps devs build powerful apps and features that use images and videos. With our cutting-edge AI tech, folks can recognize things in the world with high accuracy and deep granularity, right out of the box. No more arduous process of annotating any training data or doing any machine learning work themselves.\r",
        "batch": "W24",
        "company type": "Active",
        "industry tags": [
            "artificial-intelligence",
            "developer-tools",
            "computer-vision",
            "ml"
        ],
        "Location": "New York",
        "website": "https://dragoneye.ai/",
        "Founded": "2023",
        "Team Size": "2",
        "social media profiles": {
            "LinkedIn": null,
            "Twitter": null,
            "Facebook": null,
            "Crunchbase": null
        }
    },
    

{
    "company": {
        "Company Name": "Konstructly",
        "Tagline": "The Modern Operating System for Construction",
        "Description": "Konstructly is the first piece of software for general contractors which ties payments to work approvals. It makes it possible to accurately assess what's been built on site and how much should be paid. \r",
        "batch": "W24",
        "company type": "Active",
        "industry tags": [
            "fintech",
            "saas",
            "construction",
            "b2b",
            "enterprise"
        ],
        "Location": "London, United Kingdom",
        "website": "https://konstructly.com/",
        "Founded": "2023",
        "Team Size": "6",
        "social media profiles": {
            "LinkedIn": "https://www.linkedin.com/company/konstructly/",
            "Twitter": null,
            "Facebook": null,
            "Crunchbase": "https://www.google.com/search?q=konstructly+crunchbase&rlz=1C5CHFA_enRS948RS948&oq=konstruct

...

bio not found
{
    "company": {
        "Company Name": "DigitWhiz",
        "Tagline": "",
        "Description": "DigitWhiz is all about making sure that kids master foundational math skills in a fun and effective way. Our online program evaluates current abilities, prescribes games and guides kids to master basic and pre-algebra skills. It\u2019s easy for teachers to setup their class, get started right away and track student progress. Parents use DigitWhiz too! Check out our iPad version here. DigitWhiz is teacher created and kid approved!",
        "batch": "IK12",
        "company type": "Active",
        "industry tags": [],
        "Location": "",
        "website": "http://www.digitwhiz.com",
        "Founded": "",
        "Team Size": "2",
        "social media profiles": {
            "LinkedIn": null,
            "Twitter": null,
            "Facebook": null,
            "Crunchbase": "https://www.crunchbase.com/organization/digitwhiz"
        }
    },
    "founders": [
  

{
    "company": {
        "Company Name": "Goalbook",
        "Tagline": "Web application for teachers to plan instruction. SaaS to US K-12\u2026",
        "Description": "At Goalbook, we empower teachers to transform instruction so that ALL students succeed. We partner with over 1000 districts across 46 states, working closely with school and district leaders to scale and sustain improved instructional practice. Founded by former teachers and administrators, Goalbook was part of YC Edtech's inaugural class and the first company funded through New Schools'\u200b Seed Fund, now Reach Capital.",
        "batch": "IK12",
        "company type": "Active",
        "industry tags": [
            "education",
            "saas"
        ],
        "Location": "San Mateo, CA",
        "website": "http://goalbookapp.com",
        "Founded": "2011",
        "Team Size": "100",
        "social media profiles": {
            "LinkedIn": "https://www.linkedin.com/company/goalbook",
            "Twi

bio not found
{
    "company": {
        "Company Name": "Alieo Games",
        "Tagline": "",
        "Description": "Creative Learning Through Play! We make games that tap into innate desires for achievement and creative expression. We use artificial intelligence to personalize the learning experience to the individual. We are enabling a new generation of confident and enthusiastic learners.",
        "batch": "IK12",
        "company type": "Inactive",
        "industry tags": [],
        "Location": "Edmonton, Canada",
        "website": "http://www.alieogames.com/",
        "Founded": "",
        "Team Size": "2",
        "social media profiles": {
            "LinkedIn": null,
            "Twitter": null,
            "Facebook": null,
            "Crunchbase": null
        }
    },
    "founders": [
        {
            "Name": [],
            "Biography": [],
            "LinkedIn Profile": null,
            "Twitter Profile": null
        }
    ]
}
{
    "company": {
        "

bio not found
{
    "company": {
        "Company Name": "ClassroomIQ",
        "Tagline": "Automatically grade any paper-based assessment online.",
        "Description": "ClassroomIQ is the world's first open response grading platform that doesn't require QR codes or pre-designed templates.  All the existing materials at an educator's disposal can be used as is, without modification.  ",
        "batch": "IK12",
        "company type": "Inactive",
        "industry tags": [],
        "Location": "Chicago, IL",
        "website": "http://www.getclassroomiq.com",
        "Founded": "",
        "Team Size": "2",
        "social media profiles": {
            "LinkedIn": null,
            "Twitter": null,
            "Facebook": null,
            "Crunchbase": null
        }
    },
    "founders": [
        {
            "Name": [],
            "Biography": [],
            "LinkedIn Profile": "https://www.linkedin.com/in/stevedillinger",
            "Twitter Profile": null
        }
    

bio not found
{
    "company": {
        "Company Name": "Blendspace",
        "Tagline": "",
        "Description": "Over 10,000 schools are using Blendspace as the easiest way to create and deliver digital lessons that adapt to students needs.",
        "batch": "IK12",
        "company type": "Inactive",
        "industry tags": [],
        "Location": "San Francisco",
        "website": "http://www.blendspace.com",
        "Founded": "",
        "Team Size": "2",
        "social media profiles": {
            "LinkedIn": null,
            "Twitter": null,
            "Facebook": null,
            "Crunchbase": "https://www.crunchbase.com/organization/blendspace"
        }
    },
    "founders": [
        {
            "Name": [],
            "Biography": [],
            "LinkedIn Profile": "https://www.linkedin.com/in/gabceb",
            "Twitter Profile": "https://twitter.com/gabceb"
        }
    ]
}
bio not found
{
    "company": {
        "Company Name": "MommaZoo",
        "T

In [ ]:
output_file = "company_data.json"
with open(output_file, "w") as f:
    json.dump(all_company_data, f, indent=4)

print(f"Company data saved to {output_file}")